In [423]:
# Imports
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
import sklearn


In [424]:
# Import data
df = pd.read_csv('data/train.csv')
# Reduce dataframe the number of lines by half
df = df.sample(frac=0.1)

In [425]:
# Analyze data
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 96733 entries, 529839 to 195393
Data columns (total 14 columns):
 #   Column                         Non-Null Count  Dtype 
---  ------                         --------------  ----- 
 0   auctionId                      96733 non-null  object
 1   timeStamp                      96733 non-null  int64 
 2   placementId                    96733 non-null  int64 
 3   websiteId                      96733 non-null  int64 
 4   hashedRefererDeepThree         95175 non-null  object
 5   country                        96688 non-null  object
 6   opeartingSystem                96733 non-null  object
 7   browser                        96733 non-null  object
 8   browserVersion                 83729 non-null  object
 9   device                         96733 non-null  object
 10  environmentType                96733 non-null  object
 11  integrationType                96733 non-null  int64 
 12  articleSafenessCategorization  96733 non-null  object


In [426]:
df.head()

auctionId   timeStamp  \
529839  a922bb74-cea6-4060-b8ec-a6258a5765fa_da583d32-...  1604109460   
335328  03a1fac7-76c0-4ca0-b6d8-43aefffa3407_1f60cbfc-...  1604075146   
64708   068f5e48-4aaa-41b3-897d-fb8453997a54_671e42ab-...  1604166207   
387667  c7371be2-d5f0-42db-b5ea-b06e9c2159d0_7c9ec642-...  1603949413   
895562               9614cf3f-dc28-4a2a-a322-d23f36309f8f  1604001521   

        placementId  websiteId  \
529839       132187      73831   
335328       108383      57369   
64708        121842      68951   
387667       123249      51758   
895562        43888      29988   

                                   hashedRefererDeepThree country  \
529839  7c4266ed8cbd4348ab669fcd86c24e4b04cadc9a183f21...      FR   
335328  12a12f4ac87dc1d7dc93b5edac248b99ab473327696a74...      IT   
64708   8c07cd7ddf2a52b7806ec328b0f15231178d12c6c67cbd...      US   
387667  22608a14bf045f6f05c3879056949e5c13e502123df5f5...      FR   
895562  3fffbbaf232ab3199228b4ec6387f0cdbc67881374d42c...      CL   

       opeartingSystem                 browser browserVersion  device  \
529839         Android           Chrome Mobile           86_0   Phone   
335328         Android  Mobile Samsung Browser           12_1   Phone   
64708              iOS            Facebook App            NaN   Phone   
387667             iOS              Google App          130_0  Tablet   
895562         Android           Chrome Mobile           86_0   Phone   

       environmentType  integrationType articleSafenessCategorization  isSold  
529839          js-web                2                          safe    True  
335328          js-web                2                         uncat   False  
64708           js-web                2                          safe   False  
387667          js-web                2                         uncat    True  
895562          js-web                1                         uncat    True

In [427]:
df.describe()

timeStamp    placementId     websiteId  integrationType
count  9.673300e+04   96733.000000  96733.000000     96733.000000
mean   1.603977e+09  114118.265545  57726.846361         1.807760
std    1.760116e+05   17582.328303  14183.019556         0.394063
min    1.603670e+09   18341.000000  13734.000000         1.000000
25%    1.603824e+09  108383.000000  49049.000000         2.000000
50%    1.603978e+09  120940.000000  60789.000000         2.000000
75%    1.604133e+09  124501.000000  68951.000000         2.000000
max    1.604275e+09  133227.000000  74115.000000         2.000000

In [428]:
# get every unique value in the column 'opeartingSystem'
df.opeartingSystem.unique()


array(['Android', 'iOS', 'Linux', 'macOS', 'Windows', 'Chrome OS', 'OS X',
       'Fire OS', 'unknown', 'BSD', 'Tizen'], dtype=object)

In [429]:
# Histogram of the column 'opeartingSystem'
fig = px.histogram(df, x='opeartingSystem').update_xaxes(categoryorder='total descending')
fig.show()

In [430]:
# get every unique value in the column 'browser'
df.browser.unique()
# get the count of unique values in the column 'browser'
df.browser.nunique()

77

In [431]:
# Histogram of the column 'browser'
fig = px.histogram(df, x='browser').update_xaxes(categoryorder="total descending")
fig.show()

In [432]:
# Histogram of the column 'country'
fig = px.histogram(df, x='country').update_xaxes(categoryorder="total descending")
fig.show()

In [433]:
# Convert country code 'UK' to 'GB'
df['country'] = df['country'].replace('UK', 'GB')

In [434]:
# Histogram of the column 'timestamp'
fig = px.histogram(df, x='timeStamp')
fig.show()

In [435]:
# Function that converts the timestamp to a datetime object
def convert_timestamp(timestamp):
    date = pd.to_datetime(timestamp, unit='s')
    # extract the hour from the timestamp
    hour = date.hour
    return hour

In [436]:
# Convert the timestamp to a datetime object
df['time'] = df['timeStamp'].apply(convert_timestamp)

In [437]:
# Histogram of the column 'time'
df_fr = df[df['country'] == 'US']
fig = px.histogram(df_fr, x='time', color='isSold').update_xaxes(categoryorder="total descending")
fig.show()

In [438]:
# For each hour, count the number of sold ads
hour_count = df_fr.groupby('time')['isSold'].mean()
    
# Plot the number
fig = px.bar(hour_count, x=hour_count.index, y=hour_count.values).update_xaxes(categoryorder="total descending")
fig.show()

In [439]:
# For each country, create a individual datatframe with the mean of the sold ads for each hour
# Get all individual country
country_list = df.country.unique()

# Concatenate time and country columns to create a new dataframe
df['time_country'] = df['country'].astype(str) + '_' + df['time'].astype(str)

# Show the first 5 rows of the dataframe
df.head()


auctionId   timeStamp  \
529839  a922bb74-cea6-4060-b8ec-a6258a5765fa_da583d32-...  1604109460   
335328  03a1fac7-76c0-4ca0-b6d8-43aefffa3407_1f60cbfc-...  1604075146   
64708   068f5e48-4aaa-41b3-897d-fb8453997a54_671e42ab-...  1604166207   
387667  c7371be2-d5f0-42db-b5ea-b06e9c2159d0_7c9ec642-...  1603949413   
895562               9614cf3f-dc28-4a2a-a322-d23f36309f8f  1604001521   

        placementId  websiteId  \
529839       132187      73831   
335328       108383      57369   
64708        121842      68951   
387667       123249      51758   
895562        43888      29988   

                                   hashedRefererDeepThree country  \
529839  7c4266ed8cbd4348ab669fcd86c24e4b04cadc9a183f21...      FR   
335328  12a12f4ac87dc1d7dc93b5edac248b99ab473327696a74...      IT   
64708   8c07cd7ddf2a52b7806ec328b0f15231178d12c6c67cbd...      US   
387667  22608a14bf045f6f05c3879056949e5c13e502123df5f5...      FR   
895562  3fffbbaf232ab3199228b4ec6387f0cdbc67881374d42c...      CL   

       opeartingSystem                 browser browserVersion  device  \
529839         Android           Chrome Mobile           86_0   Phone   
335328         Android  Mobile Samsung Browser           12_1   Phone   
64708              iOS            Facebook App            NaN   Phone   
387667             iOS              Google App          130_0  Tablet   
895562         Android           Chrome Mobile           86_0   Phone   

       environmentType  integrationType articleSafenessCategorization  isSold  \
529839          js-web                2                          safe    True   
335328          js-web                2                         uncat   False   
64708           js-web                2                          safe   False   
387667          js-web                2                         uncat    True   
895562          js-web                1                         uncat    True   

        time time_country  
529839     1         FR_1  
335328    16        IT_16  
64708     17        US_17  
387667     5         FR_5  
895562    19        CL_19

In [440]:
# get timezone for each country
from datetime import datetime, tzinfo
from dateutil import tz
import pytz
# Create a function that returns the local time for a gevin country
def get_local_time(country, time):
    dt_str = pd.to_datetime(time, unit='s').strftime('%m/%d/%Y %H:%M:%S')
    format = "%m/%d/%Y %H:%M:%S"
    # Create datetime object in local timezone
    dt = datetime.strptime(dt_str, format)
    # Create datetime object in UTC timezone
    dt_utc = dt.replace(tzinfo=pytz.UTC)
    # Create datetime object in country timezone
    try:
        country_tz = pytz.country_timezones(country)[0]
        dt_country = dt_utc.astimezone(pytz.timezone(country_tz))
        return dt_country.strftime('%H')
    except:
        return pd.NaT


In [441]:
# Create a new column with the local time for each country
df['local_time'] = df.apply(lambda row: get_local_time(row['country'], row['timeStamp']), axis=1)


In [442]:
# Count the number of NaN values in the column 'local_time'
df['local_time'].isna().sum()

45

In [443]:
# For each hour, count the number of sold ads
hour_count = df.groupby('local_time')['isSold'].mean()

fig = px.bar(hour_count, x=hour_count.index, y=hour_count.values).update_xaxes(categoryorder="total descending")
fig.show()

In [458]:
# Function that returns 'neutral' if the value is between 02 and 08
def neutral(hour):
    if hour == '02' or hour == '03' or hour == '04' or hour == '05' or hour == '06' or hour == '07' or hour == '08':
        return 'neutral'

# Apply the function to the column 'local_time'
df['local_time'] = df['local_time'].apply(neutral)

# Function that returns 'bad' if the value is between 18 and 23
def bad(hour):
    if hour == '18' or hour == '19' or hour == '20' or hour == '21' or hour == '22' or hour == '23':
        return 'bad'

# Apply the function to the column 'local_time'
df['local_time'] = df['local_time'].apply(bad)


In [459]:
# get_dumy for the column 'local_time'
df_dumy = pd.get_dummies(df['local_time'])

In [460]:
# Show the first 5 rows of the dataframe
df_dumy.head()

Empty DataFrame
Columns: []
Index: [529839, 335328, 64708, 387667, 895562]

In [446]:
# Make a prediction model based on the data
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    df[['local_time_0', 'local_time_4', 'local_time_5', 'local_time_6', 'local_time_9', 'local_time_10', 'local_time_11', 'local_time_12_13_14_15', 'local_time_16', 'local_time_17', 'local_time_18', 'local_time_19', 'local_time_20', 'local_time_21', 'local_time_22_23']], 
    df['isSold'], 
    test_size=0.2, 
    random_state=0)

In [451]:
# Fit the model
model = RandomForestClassifier()
model.fit(X_train, y_train)

RandomForestClassifier()

In [452]:
# compute the score
model.score(X_test, y_test)

0.5550731379542048